# RSI Scalping Strategy 15min

In [42]:
import pandas as pd
df = pd.read_csv("EURUSD_Candlestick_1_Hour_BID_05.05.2003-08.02.2022.csv")
df.head()

Local time     Open     High      Low    Close  \
0  05.05.2003 00:00:00.000 GMT+0300  1.12284  1.12338  1.12242  1.12305   
1  05.05.2003 01:00:00.000 GMT+0300  1.12274  1.12302  1.12226  1.12241   
2  05.05.2003 02:00:00.000 GMT+0300  1.12235  1.12235  1.12160  1.12169   
3  05.05.2003 03:00:00.000 GMT+0300  1.12161  1.12314  1.12154  1.12258   
4  05.05.2003 04:00:00.000 GMT+0300  1.12232  1.12262  1.12099  1.12140   

       Volume  
0  29059.0996  
1  26091.8008  
2  29240.9004  
3  29914.8008  
4  28370.6992

In [43]:
df=df[df['Volume']!=0]
df.isna().sum()
df.reset_index(drop=True, inplace=True)
df.tail()

Local time     Open     High      Low    Close  \
117223  08.02.2022 18:00:00.000 GMT+0200  1.14182  1.14207  1.14095  1.14148   
117224  08.02.2022 19:00:00.000 GMT+0200  1.14148  1.14233  1.14146  1.14207   
117225  08.02.2022 20:00:00.000 GMT+0200  1.14206  1.14227  1.14014  1.14225   
117226  08.02.2022 21:00:00.000 GMT+0200  1.14226  1.14237  1.14114  1.14144   
117227  08.02.2022 22:00:00.000 GMT+0200  1.14143  1.14205  1.14130  1.14187   

          Volume  
117223  0.003441  
117224  0.001836  
117225  0.002602  
117226  0.002064  
117227  0.001871

In [44]:
import pandas_ta as ta
df["EMA200"] = ta.ema(df.Close, length=200)
df["RSI"] = ta.rsi(df.Close, length=3)
df['ATR']= df.ta.atr()

In [45]:
df.tail()

Local time     Open     High      Low    Close  \
117223  08.02.2022 18:00:00.000 GMT+0200  1.14182  1.14207  1.14095  1.14148   
117224  08.02.2022 19:00:00.000 GMT+0200  1.14148  1.14233  1.14146  1.14207   
117225  08.02.2022 20:00:00.000 GMT+0200  1.14206  1.14227  1.14014  1.14225   
117226  08.02.2022 21:00:00.000 GMT+0200  1.14226  1.14237  1.14114  1.14144   
117227  08.02.2022 22:00:00.000 GMT+0200  1.14143  1.14205  1.14130  1.14187   

          Volume    EMA200        RSI       ATR  
117223  0.003441  1.135455  49.972908  0.001425  
117224  0.001836  1.135521  66.835257  0.001385  
117225  0.002602  1.135588  71.267274  0.001439  
117226  0.002064  1.135646  37.468749  0.001424  
117227  0.001871  1.135708  54.609999  0.001376

## EMA Signal

In [46]:
emasignal = [0]*len(df)
backcandles = 8

for row in range(backcandles-1, len(df)):
    upt = 1
    dnt = 1
    for i in range(row-backcandles, row+1):
        if df.High[row]>=df.EMA200[row]:
            dnt=0
        if df.Low[row]<=df.EMA200[row]:
            upt=0
    if upt==1 and dnt==1:
        #print("!!!!! check trend loop !!!!")
        emasignal[row]=3
    elif upt==1:
        emasignal[row]=2
    elif dnt==1:
        emasignal[row]=1

df['EMAsignal'] = emasignal

## Total signal

In [47]:
TotSignal = [0] * len(df)
for row in range(0, len(df)):
    TotSignal[row] = 0
    if df.EMAsignal[row]==1 and df.RSI[row]>=90:
        TotSignal[row]=1
    if df.EMAsignal[row]==2 and df.RSI[row]<=10:
        TotSignal[row]=2

df['TotSignal']=TotSignal

df.dropna(inplace=True)
df.reset_index(drop=True, inplace=True)

## Visualizing signals on chart

In [48]:
import numpy as np
def pointpos(x):
    if x['TotSignal']==1:
        return x['High']+1e-3
    elif x['TotSignal']==2:
        return x['Low']-1e-3
    else:
        return np.nan

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

In [49]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from datetime import datetime

months = 24*30
startid = 0
dfpl = df[startid:startid+int(0.4*months)]

fig = go.Figure(data=[go.Candlestick(x=dfpl.index,
                open=dfpl['Open'],
                high=dfpl['High'],
                low=dfpl['Low'],
                close=dfpl['Close']),
                go.Scatter(x=dfpl.index, y=dfpl.EMA200, line=dict(color='red', width=1), name="EMA200")])

fig.add_scatter(x=dfpl.index, y=dfpl['pointpos'], mode="markers",
                marker=dict(size=5, color="MediumPurple"),
                name="Signal")
fig.show()

In [50]:
df[98:99]

Local time     Open     High      Low    Close  \
98  21.05.2003 09:00:00.000 GMT+0300  1.17101  1.17168  1.17017  1.17046   

        Volume    EMA200        RSI       ATR  EMAsignal  TotSignal  pointpos  
98  27525.9004  1.154184  17.661651  0.002144          2          0       NaN

## Backtesting Strategy

In [51]:
months = 24*30
startid = 0
dfpl = df[startid:startid+30*months]

def SIGNAL():
    return dfpl.TotSignal

In [52]:
from backtesting import Strategy
class MyStrat(Strategy):
    initsize = 0.2
    mysize = initsize
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next()
        
        #if(self.signal1>0 and len(self.trades)==0 and len(self.closed_trades)>0 and self.closed_trades[-1].pl < 0):
        #    self.mysize=self.mysize*2
        #elif len(self.closed_trades)>0 and self.closed_trades[-1].pl > 0:
        #    self.mysize=self.initsize

        if self.signal1==2 and len(self.trades)==0:   
            sl1 = self.data.Close[-1] - 100e-4
            tp1 = self.data.Close[-1] + 100e-4 
            self.buy(sl=sl1, tp=tp1, size=self.mysize)
        
        elif self.signal1==1 and len(self.trades)==0:         
            sl1 = self.data.Close[-1] + 100e-4
            tp1 = self.data.Close[-1] - 100e-4 
            self.sell(sl=sl1, tp=tp1, size=self.mysize)

In [53]:
from backtesting import Backtest

bt = Backtest(dfpl, MyStrat, cash=100, margin=1/50, commission=.00)
stat = bt.run()
stat

D:\ProgramFiles\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: UserWarning:

Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.



Start                                     0.0
End                                   21599.0
Duration                              21599.0
Exposure Time [%]                   43.189815
Equity Final [$]                     13.10049
Equity Peak [$]                     117.64099
Return [%]                          -86.89951
Buy & Hold Return [%]               10.576486
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Max. Drawdown [%]                  -88.903664
Avg. Drawdown [%]                  -12.892936
Max. Drawdown Duration                17539.0
Avg. Drawdown Duration            1784.416667
# Trades                                188.0
Win Rate [%]                        45.744681
Best Trade [%]                       0.917953
Worst Trade [%]                     -1.271054
Avg. Trade [%]                    

In [54]:
bt.plot(show_legend=False)

Row(id='6954', ...)

In [55]:
#ATR related SL TP
months = 24*30
startid = 0
dfpl = df[startid:startid+30*months]
from backtesting import Strategy
from backtesting import Backtest
class MyStrat(Strategy):
    initsize = 0.2
    mysize = initsize
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next()
        slatr = 1.3*self.data.ATR[-1]
        TPSLRatio = 1.3
        #if(self.signal1>0 and len(self.trades)==0 and len(self.closed_trades)>0 and self.closed_trades[-1].pl < 0):
        #    self.mysize=self.mysize*2
        #elif len(self.closed_trades)>0 and self.closed_trades[-1].pl > 0:
        #    self.mysize=self.initsize

        if self.signal1==2 and len(self.trades)==0:   
            sl1 = self.data.Close[-1] - slatr
            tp1 = self.data.Close[-1] + slatr*TPSLRatio
            self.buy(sl=sl1, tp=tp1, size=self.mysize)
        
        elif self.signal1==1 and len(self.trades)==0:         
            sl1 = self.data.Close[-1] + slatr
            tp1 = self.data.Close[-1] - slatr*TPSLRatio
            self.sell(sl=sl1, tp=tp1, size=self.mysize)

bt = Backtest(dfpl, MyStrat, cash=100, margin=1/50, commission=.00)
stat = bt.run()
stat

D:\ProgramFiles\Anaconda3\lib\site-packages\ipykernel_launcher.py:33: UserWarning:

Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.



Start                                     0.0
End                                   21599.0
Duration                              21599.0
Exposure Time [%]                    9.893519
Equity Final [$]                   114.521153
Equity Peak [$]                    158.009997
Return [%]                          14.521153
Buy & Hold Return [%]               10.576486
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Max. Drawdown [%]                  -28.223464
Avg. Drawdown [%]                   -5.077496
Max. Drawdown Duration                 8522.0
Avg. Drawdown Duration             669.870968
# Trades                                320.0
Win Rate [%]                          45.3125
Best Trade [%]                       0.455307
Worst Trade [%]                     -0.417412
Avg. Trade [%]                    

In [56]:
bt.plot(show_legend=False)

Row(id='7740', ...)

In [57]:
#Trailing SL with ATR related distance
months = 24*30
startid = 0
dfpl = df[startid:startid+30*months]
from backtesting import Strategy, Backtest
import numpy as np

class MyStrat(Strategy):
    initsize = 0.2
    mysize = initsize
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next()
        sltr = 1.5*self.data.ATR[-1]
        
        #if(self.signal1>0 and len(self.trades)==0 and len(self.closed_trades)>0 and self.closed_trades[-1].pl < 0):
        #    self.mysize=self.mysize*2
        #elif len(self.closed_trades)>0 and self.closed_trades[-1].pl > 0:
        #    self.mysize=self.initsize

        
        for trade in self.trades: 
            if trade.is_long: 
                trade.sl = max(trade.sl or -np.inf, self.data.Close[-1] - sltr)
                if self.signal1==1:
                    trade.close()
            else:
                trade.sl = min(trade.sl or np.inf, self.data.Close[-1] + sltr) 
                if self.signal1==2:
                    trade.close()
                    
        if self.signal1==2 and len(self.trades)==0:
            sl1 = self.data.Close[-1] - sltr
            self.buy(sl=sl1, size=self.mysize)
        elif self.signal1==1 and len(self.trades)==0:
            sl1 = self.data.Close[-1] + sltr
            self.sell(sl=sl1, size=self.mysize)


bt = Backtest(dfpl, MyStrat, cash=100, margin=1/50, commission=.000)
stat = bt.run()
stat

D:\ProgramFiles\Anaconda3\lib\site-packages\ipykernel_launcher.py:43: UserWarning:

Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.



Start                                     0.0
End                                   21599.0
Duration                              21599.0
Exposure Time [%]                   13.550926
Equity Final [$]                    91.375073
Equity Peak [$]                    161.381529
Return [%]                          -8.624927
Buy & Hold Return [%]               10.576486
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Max. Drawdown [%]                  -45.177296
Avg. Drawdown [%]                   -5.239447
Max. Drawdown Duration                17474.0
Avg. Drawdown Duration             741.827586
# Trades                                318.0
Win Rate [%]                        36.792453
Best Trade [%]                       1.510057
Worst Trade [%]                     -0.369334
Avg. Trade [%]                    

In [58]:
bt.plot()

Row(id='8526', ...)